# Test of GAT
- use DGL
- large repeating time

In [1]:
import dgl
import json
import torch
import torch as th
from tqdm import tqdm
import torch.nn as nn
from dgl.nn import GraphConv, GATConv
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
from transformers import get_linear_schedule_with_warmup

- check the GPU and assign the GPU by the best memory usage

In [2]:
import subprocess
import torch

def get_free_gpu():
    try:
        # Run nvidia-smi command to get GPU details
        _output_to_list = lambda x: x.decode('ascii').split('\n')[:-1]
        command = "nvidia-smi --query-gpu=memory.free --format=csv,nounits,noheader"
        memory_free_info = _output_to_list(subprocess.check_output(command.split())) 
        memory_free_values = [int(x) for i, x in enumerate(memory_free_info)]
        
        # Get the GPU with the maximum free memory
        best_gpu_id = memory_free_values.index(max(memory_free_values))
        return best_gpu_id
    except:
        # If any exception occurs, default to GPU 0 (this handles cases where nvidia-smi isn't installed)
        return 0

if torch.cuda.is_available():
    # Get the best GPU ID based on free memory and set it
    best_gpu_id = get_free_gpu()
    device = torch.device(f"cuda:{best_gpu_id}")
else:
    device = torch.device("cpu")
    print("there's no available GPU")

print(device)


cuda:2


## Fix the seed

In [3]:
import numpy as np
import torch
import random

#fix seed
def same_seeds(seed = 8787):
    torch.manual_seed(seed)
    # random.seed(seed) 
    if torch.cuda.is_available():
        torch.cuda.manual_seed(seed)
        torch.cuda.manual_seed_all(seed)  
    np.random.seed(seed)  
    torch.backends.cudnn.benchmark = False
    torch.backends.cudnn.deterministic = True

## Data Loader

In [4]:
class GraphDataset(Dataset):
    def __init__(self, data_list, device):
        self.data_list = data_list
        self.device = device

    def __len__(self):
        return len(self.data_list)
    
    def __getitem__(self, idx):
        data = self.data_list[idx]

        g = dgl.graph((th.tensor(data["edge_index"][0]), th.tensor(data["edge_index"][1])), num_nodes=data["num_nodes"]).to(self.device)

        g.ndata['feat'] = th.tensor(data["node_feat"]).to(self.device)
        g.edata['feat'] = th.tensor(data["edge_attr"]).to(self.device)  # Add edge features to graph

        return g, th.tensor(data["label"]).to(self.device)


def collate(samples):
    # The input `samples` is a list of pairs
    #  (graph, label).
    graphs, labels = map(list, zip(*samples))
    batched_graph = dgl.batch(graphs)
    return batched_graph, torch.tensor(labels)


In [5]:
pwd

'/workdir/home/bai/dgl/code'

In [6]:
datasets = ['train', 'valid', 'test']
dataloaders = {}

for dataset_name in tqdm(datasets):
    file_path = f"../../data_processing/dgl/data/test/repeated_{dataset_name}.jsonl"
    
    print(file_path)
#     with open(file_path) as f:
#         data_list = [json.loads(line) for line in f]
    with open(file_path) as f:
        data_list = []
        for line in tqdm(f, position=0, leave=True):
            data_list.append(json.loads(line))
#             data_list = [json.loads(line) for line in f]
#             try:
#                 data_list.append(json.loads(line))
#             except json.JSONDecodeError:
#                 continue

    
    dataset = GraphDataset(data_list, device)
    dataloaders[dataset_name] = DataLoader(dataset, batch_size=4, shuffle=False, collate_fn=collate)
    
print("Done!")

  0%|          | 0/3 [00:00<?, ?it/s]

../../data_processing/dgl/data/test/repeated_train.jsonl


1020000it [08:54, 1910.08it/s]
 33%|███▎      | 1/3 [08:54<17:48, 534.01s/it]

../../data_processing/dgl/data/test/repeated_valid.jsonl


51it [00:00, 2420.39it/s]


../../data_processing/dgl/data/test/repeated_test.jsonl


51it [00:00, 2326.47it/s]
100%|██████████| 3/3 [08:54<00:00, 178.02s/it]

Done!


### Model

In [7]:
class GAT(nn.Module):
    def __init__(self, in_dim, hidden_dim, out_dim, num_heads, dropout_prob=0.25):
        super(GAT, self).__init__()
        
        # do not check the zero in_degree since we have all the complete graph
        self.layer1 = GATConv(in_dim, hidden_dim, num_heads=num_heads, activation=F.relu, allow_zero_in_degree=True)
        self.layer2 = GATConv(hidden_dim * num_heads, out_dim, num_heads=num_heads, allow_zero_in_degree=True)
        
        # Adding Batch Normalization after each GAT layer
        self.batchnorm1 = nn.BatchNorm1d(hidden_dim * num_heads)
        self.batchnorm2 = nn.BatchNorm1d(out_dim)
        
        # Adding Dropout for regularization
        self.dropout = nn.Dropout(dropout_prob)

    def forward(self, g, h):
        # Apply GAT layers
        h = self.layer1(g, h)
        h = h.view(h.shape[0], -1)
        h = F.relu(h)
        h = self.dropout(h)
        h = self.layer2(g, h).squeeze(1)
        
        # Store the output as a new node feature
        g.ndata['h_out'] = h

        # Use mean pooling to aggregate this new node feature
        h_agg = dgl.mean_nodes(g, feat='h_out')
        return h_agg

    

- Model Forward  

In [8]:
def model_fn(data, model, criterion, device, count=1):
    """Forward a batch through the model."""
    batched_g, labels = data
#     print(batch_g)
    batched_g = batched_g.to(device)
    
    labels = labels.to(device)
    logits = model(batched_g, batched_g.ndata['feat'].float()) # for GAT
    logits = logits.mean(dim=1)
#     print(logits)
    
    loss = criterion(logits, labels)
#     print(batched_g.ndata['feat'].dtype)
#     print("Logits shape:", logits.shape)  # Expected: (batch_size, 168)
#     print("Labels shape:", labels.shape)  # Expected: (batch_size)

    # Get the class id with the highest probability.
    preds = logits.argmax(1)
    
    # Compute accuracy.
    accuracy = torch.mean((preds == labels).float())
    
    print(f"labels: {labels}", labels.shape)
    print(f"predicted: {preds}", preds.shape)

#     return loss, accuracy
    return loss, accuracy, preds

### Training

- Fix the seed and save the model.state_dict that contains the initial weight

In [ ]:
seed = 8787
same_seeds(seed)

model = GAT(in_dim=50, hidden_dim=16, out_dim=168, num_heads=8)
torch.save(model.state_dict(), 'model1_initial/initial_weight.pth')

In [ ]:
model.layer1.fc.weight

- Check if model really load the model_dict

In [ ]:
model = GAT(in_dim=50, hidden_dim=16, out_dim=168, num_heads=8)
model.load_state_dict(torch.load('model1_initial/initial_weight.pth'))
model.layer1.fc.weight

- 10 APs same as above x 5000 times and batch size = 1

In [13]:
same_seeds(seed)

model = GAT(in_dim=50, hidden_dim=16, out_dim=168, num_heads=8)
# in_dim means the dimension of the node_feat(50 dim, since the 50-dim embedding)
# out_dim means the # of the categories -> 168 for out tasks
model.load_state_dict(torch.load('model1_initial/initial_weight.pth'))

model = model.to(device)

optimizer = torch.optim.AdamW(model.parameters(), lr=2e-4)
# scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=100, num_training_steps=total_steps)

criterion = nn.CrossEntropyLoss()
total_steps = 5


# Training Part
for epoch in tqdm(range(total_steps)):
    # Train
    model.train()
    total_loss = 0.0
    total_accuracy = 0.0
    num_batches = 0
    
    count = 0 
    
    for data in tqdm(dataloaders['train']):
        
        count += 1
        loss, accuracy, _ = model_fn(data, model, criterion, device, count)
        
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        total_loss += loss.item()
        total_accuracy += accuracy.item()
        num_batches += 1
        
#     scheduler.step()
    print(f"total count: {count}")
    
    avg_loss = total_loss / num_batches
    avg_accuracy = total_accuracy / num_batches

    print(f'Epoch {epoch} | Train Loss: {avg_loss:.4f} | Train Accuracy: {avg_accuracy:.4f}')

    # Validation Part
    model.eval()
    total_accuracy = 0.0
    total_loss = 0.0
    num_batches = 0

    with torch.no_grad():
        for batched_g in dataloaders['valid']:
            loss, accuracy, _ = model_fn(batched_g, model, criterion, device)
            total_accuracy += accuracy.item()
            total_loss += loss.item()
            num_batches += 1

    avg_accuracy = total_accuracy / num_batches
    avg_loss = total_loss / num_batches
    print(f'Validation Loss: {avg_loss:.4f} | Validation Accuracy: {avg_accuracy:.4f}')


    # Save checkpoint
    if epoch%20 == 0:
        torch.save({
                'epoch': epoch,
                'model_state_dict': model.state_dict(),
                'optimizer_state_dict': optimizer.state_dict(),
                'loss': loss,
                }, f"../checkpoint_GAT/checkpoint_{epoch}.pt")
    

# Testing Part
model.eval()
total = 0
correct = 0

with torch.no_grad():
    for data in dataloaders['test']:
        loss, accuracy, predicted = model_fn(data, model, criterion, device)
        labels = data[1].to(device)  # Assuming labels are the second element in the tuple
        
        print(f"labels: {labels}", labels.shape)
        print(f"predicted: {predicted}", predicted.shape)
        
        total += labels.size(0) # label.size(0) is the batch size
        correct += (predicted == labels).sum().item() 
        # (predicted == labels).sum() would return how many of them are equal; 
        # .item() would make the tensor to the regular value
        
    print('Test Accuracy: %d %%' % (100 * correct / total))

  3%|▎         | 1501/50000 [00:32<17:45, 45.51it/s]


  6%|▌         | 2979/50000 [01:05<16:41, 46.96it/s]


  9%|▉         | 4461/50000 [01:37<16:40, 45.52it/s]


 16%|█▌        | 8104/50000 [02:07<05:35, 124.90it/s]


 24%|██▎       | 11796/50000 [02:36<05:09, 123.53it/s]


...

 40%|████      | 2/5 [29:58<44:45, 895.33s/it]  

total count: 50000
Epoch 1 | Train Loss: 0.5472 | Train Accuracy: 0.7555
Validation Loss: 0.5550 | Validation Accuracy: 0.7000



  3%|▎         | 1556/50000 [00:31<16:53, 47.80it/s]


 40%|████      | 2/5 [30:32<45:48, 916.21s/it]


KeyboardInterrupt: 

- 10 APs same as above x 5000 times and batch size = 4

In [16]:
same_seeds(seed)

model = GAT(in_dim=50, hidden_dim=16, out_dim=168, num_heads=8)
# in_dim means the dimension of the node_feat(50 dim, since the 50-dim embedding)
# out_dim means the # of the categories -> 168 for out tasks
model.load_state_dict(torch.load('model1_initial/initial_weight.pth'))

model = model.to(device)

optimizer = torch.optim.AdamW(model.parameters(), lr=2e-4)
# scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=100, num_training_steps=total_steps)

criterion = nn.CrossEntropyLoss()
total_steps = 5


# Training Part
for epoch in tqdm(range(total_steps)):
    # Train
    model.train()
    total_loss = 0.0
    total_accuracy = 0.0
    num_batches = 0
    
    count = 0 
    
    for data in tqdm(dataloaders['train']):
        
        count += 1
        loss, accuracy, _ = model_fn(data, model, criterion, device, count)
        
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        total_loss += loss.item()
        total_accuracy += accuracy.item()
        num_batches += 1
        
#     scheduler.step()
    print(f"total count: {count}")
    
    avg_loss = total_loss / num_batches
    avg_accuracy = total_accuracy / num_batches

    print(f'Epoch {epoch} | Train Loss: {avg_loss:.4f} | Train Accuracy: {avg_accuracy:.4f}')

    # Validation Part
    model.eval()
    total_accuracy = 0.0
    total_loss = 0.0
    num_batches = 0

    with torch.no_grad():
        for batched_g in dataloaders['valid']:
            loss, accuracy, _ = model_fn(batched_g, model, criterion, device)
            total_accuracy += accuracy.item()
            total_loss += loss.item()
            num_batches += 1

    avg_accuracy = total_accuracy / num_batches
    avg_loss = total_loss / num_batches
    print(f'Validation Loss: {avg_loss:.4f} | Validation Accuracy: {avg_accuracy:.4f}')


    # Save checkpoint
    if epoch%20 == 0:
        torch.save({
                'epoch': epoch,
                'model_state_dict': model.state_dict(),
                'optimizer_state_dict': optimizer.state_dict(),
                'loss': loss,
                }, f"../checkpoint_GAT/checkpoint_{epoch}.pt")
    

# Testing Part
model.eval()
total = 0
correct = 0

with torch.no_grad():
    for data in dataloaders['test']:
        loss, accuracy, predicted = model_fn(data, model, criterion, device)
        labels = data[1].to(device)  # Assuming labels are the second element in the tuple
        
        print(f"labels: {labels}", labels.shape)
        print(f"predicted: {predicted}", predicted.shape)
        
        total += labels.size(0) # label.size(0) is the batch size
        correct += (predicted == labels).sum().item() 
        # (predicted == labels).sum() would return how many of them are equal; 
        # .item() would make the tensor to the regular value
        
    print('Test Accuracy: %d %%' % (100 * correct / total))

 13%|█▎        | 1621/12500 [00:32<03:35, 50.47it/s]


 25%|██▌       | 3127/12500 [01:05<03:19, 46.88it/s]


 37%|███▋      | 4630/12500 [01:37<02:49, 46.56it/s]


 49%|████▉     | 6131/12500 [02:09<02:10, 48.64it/s]


 61%|██████    | 7629/12500 [02:40<01:42, 47.75it/s]


...

 74%|███████▎  | 9195/12500 [03:12<01:10, 47.09it/s]


 86%|████████▌ | 10697/12500 [03:43<00:38, 47.24it/s]


 97%|█████████▋| 12154/12500 [04:15<00:07, 46.46it/s]


100%|██████████| 5/5 [21:45<00:00, 261.19s/it]

total count: 12500
Epoch 4 | Train Loss: 0.5204 | Train Accuracy: 0.7641
Validation Loss: 0.7038 | Validation Accuracy: 0.6667
labels: tensor([118, 121, 128, 122], device='cuda:1') torch.Size([4])
predicted: tensor([118, 121, 128, 122], device='cuda:1') torch.Size([4])
labels: tensor([120, 139,  83,  74], device='cuda:1') torch.Size([4])
predicted: tensor([120,  57,  57,  74], device='cuda:1') torch.Size([4])
labels: tensor([57,  0], device='cuda:1') torch.Size([2])
predicted: tensor([57, 57], device='cuda:1') torch.Size([2])
Test Accuracy: 70 %


- 22 APs x 5000 times and batch size = 4, model 1

In [22]:
same_seeds(seed)

model = GAT(in_dim=50, hidden_dim=16, out_dim=168, num_heads=8)
# in_dim means the dimension of the node_feat(50 dim, since the 50-dim embedding)
# out_dim means the # of the categories -> 168 for out tasks
model.load_state_dict(torch.load('model1_initial/initial_weight.pth'))

model = model.to(device)

optimizer = torch.optim.AdamW(model.parameters(), lr=2e-4)
# scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=100, num_training_steps=total_steps)

criterion = nn.CrossEntropyLoss()
total_steps = 5


# Training Part
for epoch in tqdm(range(total_steps)):
    # Train
    model.train()
    total_loss = 0.0
    total_accuracy = 0.0
    num_batches = 0
    
    count = 0 
    
    for data in tqdm(dataloaders['train']):
        
        count += 1
        loss, accuracy, _ = model_fn(data, model, criterion, device, count)
        
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        total_loss += loss.item()
        total_accuracy += accuracy.item()
        num_batches += 1
        
#     scheduler.step()
    print(f"total count: {count}")
    
    avg_loss = total_loss / num_batches
    avg_accuracy = total_accuracy / num_batches

    print(f'Epoch {epoch} | Train Loss: {avg_loss:.4f} | Train Accuracy: {avg_accuracy:.4f}')

    # Validation Part
    model.eval()
    total_accuracy = 0.0
    total_loss = 0.0
    num_batches = 0

    with torch.no_grad():
        for batched_g in dataloaders['valid']:
            loss, accuracy, _ = model_fn(batched_g, model, criterion, device)
            total_accuracy += accuracy.item()
            total_loss += loss.item()
            num_batches += 1

    avg_accuracy = total_accuracy / num_batches
    avg_loss = total_loss / num_batches
    print(f'Validation Loss: {avg_loss:.4f} | Validation Accuracy: {avg_accuracy:.4f}')


    # Save checkpoint
    if epoch%20 == 0:
        torch.save({
                'epoch': epoch,
                'model_state_dict': model.state_dict(),
                'optimizer_state_dict': optimizer.state_dict(),
                'loss': loss,
                }, f"../checkpoint_GAT/checkpoint_{epoch}.pt")
    

# Testing Part
model.eval()
total = 0
correct = 0

with torch.no_grad():
    for data in dataloaders['test']:
        loss, accuracy, predicted = model_fn(data, model, criterion, device)
        labels = data[1].to(device)  # Assuming labels are the second element in the tuple
        
        print(f"labels: {labels}", labels.shape)
        print(f"predicted: {predicted}", predicted.shape)
        
        total += labels.size(0) # label.size(0) is the batch size
        correct += (predicted == labels).sum().item() 
        # (predicted == labels).sum() would return how many of them are equal; 
        # .item() would make the tensor to the regular value
        
    print('Test Accuracy: %d %%' % (100 * correct / total))

  6%|▌         | 1577/27500 [00:32<08:46, 49.27it/s]


 12%|█▏        | 3176/27500 [01:04<08:08, 49.82it/s]


 17%|█▋        | 4793/27500 [01:37<07:34, 50.00it/s]


 23%|██▎       | 6381/27500 [02:09<07:03, 49.82it/s]


 29%|██▉       | 7993/27500 [02:41<06:26, 50.48it/s]


...

 85%|████████▌ | 23385/27500 [07:57<01:26, 47.41it/s]


 90%|█████████ | 24841/27500 [08:29<00:57, 46.16it/s]


 96%|█████████▌| 26378/27500 [09:00<00:22, 49.23it/s]


100%|██████████| 5/5 [48:20<00:00, 580.00s/it]

total count: 27500
Epoch 4 | Train Loss: 0.8906 | Train Accuracy: 0.6789
Validation Loss: 0.8371 | Validation Accuracy: 0.6667
labels: tensor([118, 121, 128, 122], device='cuda:1') torch.Size([4])
predicted: tensor([118, 121, 128, 122], device='cuda:1') torch.Size([4])
labels: tensor([120, 139,  83,  74], device='cuda:1') torch.Size([4])
predicted: tensor([120, 129, 129,  74], device='cuda:1') torch.Size([4])
labels: tensor([57,  0, 19, 17], device='cuda:1') torch.Size([4])
predicted: tensor([129, 129,  19,  17], device='cuda:1') torch.Size([4])
labels: tensor([ 31,  30,  32, 129], device='cuda:1') torch.Size([4])
predicted: tensor([129, 132, 132, 129], device='cuda:1') torch.Size([4])
labels: tensor([131, 130, 133, 132], device='cuda:1') torch.Size([4])
predicted: tensor([129, 130, 133, 132], device='cuda:1') torch.Size([4])
labels: tensor([135, 137], device='cuda:1') torch.Size([2])
predicted: tensor([135, 137], device='cuda:1') torch.Size([2])
Test Accuracy: 63 %


- 35 APs x 20000 times and batch size = 4

In [12]:
seed = 8787
same_seeds(seed)

model = GAT(in_dim=50, hidden_dim=16, out_dim=168, num_heads=8)
# in_dim means the dimension of the node_feat(50 dim, since the 50-dim embedding)
# out_dim means the # of the categories -> 168 for out tasks
model.load_state_dict(torch.load('model1_initial/initial_weight.pth'))

model = model.to(device)

optimizer = torch.optim.AdamW(model.parameters(), lr=2e-4)
# scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=100, num_training_steps=total_steps)

criterion = nn.CrossEntropyLoss()
total_steps = 5


# Training Part
for epoch in tqdm(range(total_steps)):
    # Train
    model.train()
    total_loss = 0.0
    total_accuracy = 0.0
    num_batches = 0
    
    count = 0 
    
    for data in tqdm(dataloaders['train'], position=0, leave=True):
        
        count += 1
        loss, accuracy, _ = model_fn(data, model, criterion, device, count)
        
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        total_loss += loss.item()
        total_accuracy += accuracy.item()
        num_batches += 1
        
#     scheduler.step()
    print(f"total count: {count}")
    
    avg_loss = total_loss / num_batches
    avg_accuracy = total_accuracy / num_batches

    print(f'Epoch {epoch} | Train Loss: {avg_loss:.4f} | Train Accuracy: {avg_accuracy:.4f}')

    # Validation Part
    model.eval()
    total_accuracy = 0.0
    total_loss = 0.0
    num_batches = 0

    with torch.no_grad():
        for batched_g in dataloaders['valid']:
            loss, accuracy, _ = model_fn(batched_g, model, criterion, device)
            total_accuracy += accuracy.item()
            total_loss += loss.item()
            num_batches += 1

    avg_accuracy = total_accuracy / num_batches
    avg_loss = total_loss / num_batches
    print(f'Validation Loss: {avg_loss:.4f} | Validation Accuracy: {avg_accuracy:.4f}')


    # Save checkpoint
    if epoch%20 == 0:
        torch.save({
                'epoch': epoch,
                'model_state_dict': model.state_dict(),
                'optimizer_state_dict': optimizer.state_dict(),
                'loss': loss,
                }, f"../checkpoint_GAT/checkpoint_{epoch}.pt")
    

# Testing Part
model.eval()
total = 0
correct = 0

with torch.no_grad():
    for data in dataloaders['test']:
        loss, accuracy, predicted = model_fn(data, model, criterion, device)
        labels = data[1].to(device)  # Assuming labels are the second element in the tuple
        
        print(f"labels: {labels}", labels.shape)
        print(f"predicted: {predicted}", predicted.shape)
        
        total += labels.size(0) # label.size(0) is the batch size
        correct += (predicted == labels).sum().item() 
        # (predicted == labels).sum() would return how many of them are equal; 
        # .item() would make the tensor to the regular value
        
    print('Test Accuracy: %d %%' % (100 * correct / total))

 20%|██        | 1/5 [53:47<3:35:10, 3227.61s/it]

total count: 175000
Epoch 0 | Train Loss: 1.3030 | Train Accuracy: 0.6040
Validation Loss: 0.9490 | Validation Accuracy: 0.6574


 40%|████      | 2/5 [1:46:11<2:38:54, 3178.33s/it]

total count: 175000
Epoch 1 | Train Loss: 0.8947 | Train Accuracy: 0.6888
Validation Loss: 0.9233 | Validation Accuracy: 0.6574


 60%|██████    | 3/5 [2:38:39<1:45:29, 3164.73s/it]

total count: 175000
Epoch 2 | Train Loss: 0.8521 | Train Accuracy: 0.6956
Validation Loss: 0.9145 | Validation Accuracy: 0.6852


 80%|████████  | 4/5 [3:31:00<52:35, 3155.14s/it]  

total count: 175000
Epoch 3 | Train Loss: 0.8365 | Train Accuracy: 0.6995
Validation Loss: 0.9111 | Validation Accuracy: 0.6852


100%|██████████| 5/5 [4:23:16<00:00, 3159.26s/it]


total count: 175000
Epoch 4 | Train Loss: 0.8281 | Train Accuracy: 0.7009
Validation Loss: 0.9069 | Validation Accuracy: 0.6852
labels: tensor([118, 121, 128, 122], device='cuda:1') torch.Size([4])
predicted: tensor([118, 121, 128, 122], device='cuda:1') torch.Size([4])
labels: tensor([120, 139,  83,  74], device='cuda:1') torch.Size([4])
predicted: tensor([120,   5,   5,  74], device='cuda:1') torch.Size([4])
labels: tensor([57,  0, 19, 17], device='cuda:1') torch.Size([4])
predicted: tensor([ 5,  5, 19, 17], device='cuda:1') torch.Size([4])
labels: tensor([ 31,  30,  32, 129], device='cuda:1') torch.Size([4])
predicted: tensor([ 5, 32, 32,  5], device='cuda:1') torch.Size([4])
labels: tensor([131, 130, 133, 132], device='cuda:1') torch.Size([4])
predicted: tensor([  5, 130, 133, 132], device='cuda:1') torch.Size([4])
labels: tensor([135, 137, 145, 146], device='cuda:1') torch.Size([4])
predicted: tensor([135, 137, 145, 146], device='cuda:1') torch.Size([4])
labels: tensor([147,  75, 

- 51 APs x 20000 times and batch size = 4

In [ ]:
seed = 8787
same_seeds(seed)

model = GAT(in_dim=50, hidden_dim=16, out_dim=168, num_heads=8)
# in_dim means the dimension of the node_feat(50 dim, since the 50-dim embedding)
# out_dim means the # of the categories -> 168 for out tasks
model.load_state_dict(torch.load('model1_initial/initial_weight.pth'))

model = model.to(device)

optimizer = torch.optim.AdamW(model.parameters(), lr=2e-4)
# scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=100, num_training_steps=total_steps)

criterion = nn.CrossEntropyLoss()
total_steps = 5


# Training Part
for epoch in tqdm(range(total_steps)):
    # Train
    model.train()
    total_loss = 0.0
    total_accuracy = 0.0
    num_batches = 0
    
    count = 0 
    
    for data in tqdm(dataloaders['train'], position=0, leave=True):
        
        count += 1
        loss, accuracy, _ = model_fn(data, model, criterion, device, count)
        
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        total_loss += loss.item()
        total_accuracy += accuracy.item()
        num_batches += 1
        
#     scheduler.step()
    print(f"total count: {count}")
    
    avg_loss = total_loss / num_batches
    avg_accuracy = total_accuracy / num_batches

    print(f'Epoch {epoch} | Train Loss: {avg_loss:.4f} | Train Accuracy: {avg_accuracy:.4f}')

    # Validation Part
    model.eval()
    total_accuracy = 0.0
    total_loss = 0.0
    num_batches = 0

    with torch.no_grad():
        for batched_g in dataloaders['valid']:
            loss, accuracy, _ = model_fn(batched_g, model, criterion, device)
            total_accuracy += accuracy.item()
            total_loss += loss.item()
            num_batches += 1

    avg_accuracy = total_accuracy / num_batches
    avg_loss = total_loss / num_batches
    print(f'Validation Loss: {avg_loss:.4f} | Validation Accuracy: {avg_accuracy:.4f}')


    # Save checkpoint
    if epoch%20 == 0:
        torch.save({
                'epoch': epoch,
                'model_state_dict': model.state_dict(),
                'optimizer_state_dict': optimizer.state_dict(),
                'loss': loss,
                }, f"../checkpoint_GAT/checkpoint_{epoch}.pt")
    

# Testing Part
model.eval()
total = 0
correct = 0

with torch.no_grad():
    for data in dataloaders['test']:
        loss, accuracy, predicted = model_fn(data, model, criterion, device)
        labels = data[1].to(device)  # Assuming labels are the second element in the tuple
        
        print(f"labels: {labels}", labels.shape)
        print(f"predicted: {predicted}", predicted.shape)
        
        total += labels.size(0) # label.size(0) is the batch size
        correct += (predicted == labels).sum().item() 
        # (predicted == labels).sum() would return how many of them are equal; 
        # .item() would make the tensor to the regular value
        
    print('Test Accuracy: %d %%' % (100 * correct / total))

 20%|██        | 1/5 [1:21:45<5:27:00, 4905.01s/it]

total count: 255000
Epoch 0 | Train Loss: 1.2472 | Train Accuracy: 0.6397
Validation Loss: 0.9132 | Validation Accuracy: 0.6923


 40%|████      | 2/5 [2:46:49<4:11:06, 5022.08s/it]

total count: 255000
Epoch 1 | Train Loss: 0.8826 | Train Accuracy: 0.7073
Validation Loss: 0.8933 | Validation Accuracy: 0.6923


 60%|██████    | 3/5 [4:12:55<2:49:36, 5088.05s/it]

total count: 255000
Epoch 2 | Train Loss: 0.8555 | Train Accuracy: 0.7116
Validation Loss: 0.8860 | Validation Accuracy: 0.6923


 80%|████████  | 4/5 [5:39:39<1:25:33, 5133.80s/it]

total count: 255000
Epoch 3 | Train Loss: 0.8456 | Train Accuracy: 0.7129
Validation Loss: 0.8838 | Validation Accuracy: 0.6923


 87%|████████▋ | 221687/255000 [1:14:22<11:20, 48.93it/s] 